# MetPy Intro: NYS Mesonet Map
---

## Overview
In this notebook, we'll use Cartopy, Matplotlib, and Pandas (with a bunch of help from [MetPy](https://unidata.github.io/MetPy)) to read in, manipulate, and visualize current data from the [New York State Mesonet](https://www2.nysmesonet.org).

## Prerequisites

| Concepts | Importance | Notes |
| --- | --- | --- |
| Matplotlib | Necessary | |
| Cartopy | Necessary | |
| Pandas  | Necessary | |
| MetPy | Necessary | Intro |

* **Time to learn**: 30 minutes

___
## Imports

In [ ]:
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
from datetime import datetime
from cartopy import crs as ccrs
from cartopy import feature as cfeature
from metpy.calc import wind_components, dewpoint_from_relative_humidity
from metpy.units import units
from metpy.plots import StationPlot, USCOUNTIES

Create a Pandas `DataFrame` object pointing to the most recent set of NYSM obs.

In [ ]:
nysm_data = pd.read_csv('https://www.atmos.albany.edu/products/nysm/nysm_latest.csv')

In [ ]:
nysm_data.columns

Create several `Series` objects for some of the columns.

In [ ]:
stid = nysm_data['station']
lats = nysm_data['lat']
lons = nysm_data['lon']

Our goal is to make a map of NYSM observations, which includes the wind velocity. The convention is to plot wind velocity using wind barbs. The **MetPy** library allows us to not only make such a map, but perform a variety of meteorologically-relevant calculations and diagnostics. Here, we will use such a calculation, which will determine the two scalar components of wind velocity (*u* and *v*), from wind speed and direction. We will use MetPy's [wind_components](https://unidata.github.io/MetPy/latest/api/generated/metpy.calc.wind_components.html) method. 

This method requires us to do the following:
1. Create Pandas `Series` objects for the variables of interest
1. Extract the underlying Numpy array via the `Series`' `values` attribute
1. Attach units to these arrays using MetPy's `units` class

#### Perform these three steps

In [ ]:
wspd = nysm_data['max_wind_speed_prop [m/s]'].values * units['m/s']
drct = nysm_data['wind_direction_prop [degrees]'].values * units['degree']

<div class="alert alert-info">
    <b>Tip:</b> The <b>*</b> operator might make you think that we're multiplying. However, in this case we use it to "attach" units to an array of values.</div>

Examine these two *units aware* `Series`

In [ ]:
wspd

<div class="alert alert-info">
    <b>Tip:</b> This is a unique type of object: not only does it have values, aka <i>magnitude</i>, but it also has <i>Units</i> attached. This is a very nice property, since it will make calculations that require awareness of units much easier!</div>

In [ ]:
drct

Convert wind speed from m/s to knots

In [ ]:
wspk = wspd.to('knots')

In [ ]:
wspk

#### Perform the vector decomposition

In [ ]:
u, v = wind_components(wspk, drct)

Take a look at one of the output components:

In [ ]:
u

<div class="alert alert-warning">
    <b>Exercise:</b> Create a 2-meter temperature object; attach units of degrees Celsius (<b><i>degC</i></b>) to it, and then convert <b>to</b> Fahrenheit (<b><i>degF</i></b>).</div>

In [ ]:
# Write your code here

In [1]:
#%load /spare11/atm350/common/mar12/metpy1.py

Now, let's plot several of the meteorological values on a map. We will use **Matplotlib** and **Cartopy**, as well as **MetPy**'s `StationPlot` method.

Create units-aware objects for relative humidity and station pressure

In [ ]:
rh = nysm_data['relative_humidity [percent]'].values * units('percent')
pres = nysm_data['station_pressure [mbar]'].values * units('mbar')

### Plot the map, centered over NYS, with add some geographic features, and the mesonet data.

Determine the current time, for use in the plot's title and a version to be saved to disk.

In [ ]:
timeString = nysm_data['time'][0]
timeObj = datetime.strptime(timeString,"%Y-%m-%d %H:%M:%S")
titleString = datetime.strftime(timeObj,"%B %d %Y, %H%M UTC")
figString = datetime.strftime(timeObj,"%Y%m%d_%H%M")

### Previously, we used the `ax.scatter` and `ax.text` methods to plot markers for the stations and their site id's. The latter method does not provide an intuitive means to orient several text stings relative to a central point as we typically do for a meteorological surface station plot. Let's take advantage of the `Metpy` package, and its StationPlot method!

#### <b>Be patient: this may take a minute or so to plot, if you chose the highest resolution for the shapefiles!</b>

#### Specify two resolutions: one for the Natural Earth shapefiles, and the other for MetPy's US County shapefiles.

In [ ]:
res = '10m'
resCounty = '5m'

In [ ]:
# Set the domain for defining the plot region.
latN = 45.2
latS = 40.2
lonW = -80.0
lonE = -72.0
cLat = (latN + latS)/2
cLon = (lonW + lonE )/2

proj = ccrs.LambertConformal(central_longitude=cLon, central_latitude=cLat)

fig = plt.figure(figsize=(18,12),dpi=150) # Increase the dots per inch from default 100 to make plot easier to read
ax = fig.add_subplot(1,1,1,projection=proj)
ax.set_extent ([lonW,lonE,latS,latN])
ax.set_facecolor(cfeature.COLORS['water'])
ax.add_feature (cfeature.STATES.with_scale(res))
ax.add_feature (cfeature.RIVERS.with_scale(res))
ax.add_feature (cfeature.LAND.with_scale(res))
ax.add_feature (cfeature.COASTLINE.with_scale(res))
ax.add_feature (cfeature.LAKES.with_scale(res))
ax.add_feature (cfeature.STATES.with_scale(res))

ax.add_feature(USCOUNTIES.with_scale(resCounty), linewidth=0.8, edgecolor='darkgray')

# Create a station plot pointing to an Axes to draw on as well as the location of points
stationplot = StationPlot(ax, lons, lats, transform=ccrs.PlateCarree(),
                          fontsize=8)

stationplot.plot_parameter('NW', tmpf, color='red')
stationplot.plot_parameter('SW', rh, color='green')
stationplot.plot_parameter('NE', pres, color='purple')
stationplot.plot_barb(u, v,zorder=2) # zorder value set so wind barbs will display over lake features

plotTitle = f'NYSM Temperature(°F), RH (%), Station Pressure (hPa), Peak 5-min Wind (kts), {titleString}'
ax.set_title (plotTitle);

<div class="alert alert-info">
    <b>Tip:</b> In the code cell above, the <b>plotTitle</b> string object, uses <a href="https://realpython.com/python-f-strings/">f-strings</a>, which is a newer and better way of constructing more complex string objects in Python.</div>

What if we wanted to plot sea-level pressure (SLP) instead of station pressure? In this case, we can apply what's called a **reduction to sea-level pressure** formula. This formula requires station elevation (accounting for sensor height) in meters, temperature in Kelvin, and station pressure in hectopascals. We assume each NYSM station has its sensor height .5 meters above ground level.

<div class="alert alert-info">
    <b>Tip:</b> At present, <b>MetPy</b> does not yet have a function that reduces station pressure to SLP, so we will do a <i>units-unaware</i> calculation. We can strip the units ... i.e., take only the <i>magnitude</i> of the units-aware variables via their <b><i>.m</i></b> attribute.</div>

In [ ]:
pres.m

In [ ]:
elev = nysm_data['elevation']
sensorHeight = .5
# Reduce station pressure to SLP. Source: https://www.sandhurstweather.org.uk/barometric.pdf 
slp = pres.m/np.exp(-1*(elev+sensorHeight)/((tmpc.m + 273.15) * 29.263))

In [ ]:
slp

Make a new map, substituting SLP for station pressure. We will also use the convention of the three least-significant digits to represent SLP in hectopascals.

<div class="alert alert-info">
    <b>Examples: 1018.4</b> hPa would be plotted as <b>184</b>, while <b>977.2</b> hPa would be plotted as <b>772.</b></div>

In [ ]:
fig = plt.figure(figsize=(18,12),dpi=150) # Increase the dots per inch from default 100 to make plot easier to read
ax = fig.add_subplot(1,1,1,projection=proj)
ax.set_extent ([lonW,lonE,latS,latN])
ax.set_facecolor(cfeature.COLORS['water'])
ax.add_feature (cfeature.STATES.with_scale(res))
ax.add_feature (cfeature.RIVERS.with_scale(res))
ax.add_feature (cfeature.LAND.with_scale(res))
ax.add_feature (cfeature.COASTLINE.with_scale(res))
ax.add_feature (cfeature.LAKES.with_scale(res))
ax.add_feature (cfeature.STATES.with_scale(res))

ax.add_feature(USCOUNTIES.with_scale(resCounty), linewidth=0.8, edgecolor='darkgray')

stationplot = StationPlot(ax, lons, lats, transform=ccrs.PlateCarree(),
                          fontsize=8)

stationplot.plot_parameter('NW', tmpf, color='red')
stationplot.plot_parameter('SW', rh, color='green')
# A more complex example uses a custom formatter to control how the sea-level pressure
# values are plotted. This uses the standard trailing 3-digits of the pressure value
# in tenths of millibars.
stationplot.plot_parameter('NE', slp, color='purple', formatter=lambda v: format(10 * v, '.0f')[-3:])
stationplot.plot_barb(u, v,zorder=2)
plotTitle = f'NYSM Temperature(°F), RH (%), SLP(hPa), Peak 5-min Wind (kts), {titleString}'
ax.set_title (plotTitle);


One last thing to do ... plot dewpoint instead of RH. MetPy's [dewpoint_from_relative_humidity](https://unidata.github.io/MetPy/latest/api/generated/metpy.calc.dewpoint_from_relative_humidity.html) takes care of this!

In [ ]:
dwpc = dewpoint_from_relative_humidity(tmpf, rh)

In [ ]:
dwpc

The dewpoint is returned in units of degrees Celsius, so convert to Fahrenheit.

In [ ]:
dwpf = dwpc.to('degF')

Plot the map

In [ ]:
res = '10m'
fig = plt.figure(figsize=(18,12),dpi=150) # Increase the dots per inch from default 100 to make plot easier to read
ax = fig.add_subplot(1,1,1,projection=proj)
ax.set_extent ([lonW,lonE,latS,latN])
ax.set_facecolor(cfeature.COLORS['water'])
ax.add_feature(cfeature.STATES.with_scale(res))
ax.add_feature(cfeature.RIVERS.with_scale(res))
ax.add_feature (cfeature.LAND.with_scale(res))
ax.add_feature(cfeature.COASTLINE.with_scale(res))
ax.add_feature (cfeature.LAKES.with_scale(res))
ax.add_feature (cfeature.STATES.with_scale(res))

ax.add_feature(USCOUNTIES.with_scale(resCounty), linewidth=0.8, edgecolor='darkgray')

stationplot = StationPlot(ax, lons, lats, transform=ccrs.PlateCarree(),
                          fontsize=8)

stationplot.plot_parameter('NW', tmpf, color='red')
stationplot.plot_parameter('SW', dwpf, color='green')
# A more complex example uses a custom formatter to control how the sea-level pressure
# values are plotted. This uses the standard trailing 3-digits of the pressure value
# in tenths of millibars.
stationplot.plot_parameter('NE', slp, color='purple', formatter=lambda v: format(10 * v, '.0f')[-3:])
stationplot.plot_barb(u, v,zorder=2)
plotTitle = f'NYSM Temperature and Dewpoint(°F), SLP (hPa), Peak 5-min Wind (kts), {titleString}'
ax.set_title (plotTitle);


Save the plot to the current directory.

In [ ]:
figName = f'NYSM_{figString}.png'
figName

In [ ]:
fig.savefig(figName)

---
## Summary
* The **MetPy** library provides methods to assign physical units to numerical arrays and perform units-aware calculations
* **MetPy**'s `StationPlot` method offers a customized use of **Matplotlib**'s **Pyplot** library to plot several meteorologically-relevant parameters centered about several geo-referenced points.
### What's Next?
In the next notebook, we will plot METAR observations from sites across the world, using a different access method to retrieve the data.
## Resources and References
1. [MetPy's *calc* library](https://unidata.github.io/MetPy/latest/api/generated/metpy.calc.html)
1. [MetPy's *units* library](https://unidata.github.io/MetPy/latest/api/generated/metpy.units.html)
1. [Sea-level pressure reduction formula (source: Sandhurst Weather site)](https://www.sandhurstweather.org.uk/barometric.pdf)
1. [MetPy's *StationPlot* class](https://unidata.github.io/MetPy/latest/api/generated/metpy.plots.StationPlot.html#metpy.plots.StationPlot)